In [21]:
import numpy as np
import phate
import sys
sys.path.append('../src/')
from data_script import hemisphere_data, sklearn_swiss_roll
from data_convert import convert_data
from plotly3d.plot import scatter
from negative_sampling import gradually_add
import pathlib
from scipy.spatial.distance import pdist, squareform
from diffusionmap import DiffusionMap


Generate data

In [2]:
from autometric.datasets import Hemisphere
S = Hemisphere(num_points=6000)
points = S.X.numpy()

INFO: Using pytorch backend


In [3]:
data_dict0 = convert_data(points, t=1)

Calculating PHATE...
  Running PHATE on 2947 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.14 seconds.
    Calculating affinities...
    Calculated affinities in 0.29 seconds.
  Calculated graph and diffusion operator in 0.44 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.64 seconds.
    Calculating KMeans...
    Calculated KMeans in 16.69 seconds.
  Calculated landmark operator in 19.97 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 0.11 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning: The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.
  warnings.warn(


  Calculated metric MDS in 468.13 seconds.
Calculated PHATE in 488.79 seconds.
Calculating PHATE...
  Running PHATE on 2357 observations and 3 variables.
  Calculating graph and diffusion operator...
    Calculating KNN search...
    Calculated KNN search in 0.04 seconds.
    Calculating affinities...
    Calculated affinities in 0.01 seconds.
  Calculated graph and diffusion operator in 0.09 seconds.
  Calculating landmark operator...
    Calculating SVD...
    Calculated SVD in 0.23 seconds.
    Calculating KMeans...
    Calculated KMeans in 8.03 seconds.
  Calculated landmark operator in 10.72 seconds.
  Calculating diffusion potential...
  Calculated diffusion potential in 0.01 seconds.
  Calculating metric MDS...


/gpfs/gibbs/pi/krishnaswamy_smita/xingzhi/.conda_envs/geosink/lib/python3.11/site-packages/sklearn/manifold/_mds.py:299: FutureWarning: The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.
  warnings.warn(


  Calculated metric MDS in 353.23 seconds.
Calculated PHATE in 364.36 seconds.


In [4]:
# data = np.load('../../data/hemisphere.npz')
# data_dict0 = {f:data[f] for f in data.files}

In [5]:
scatter(data_dict0['phate'], s=5)

In [6]:
scatter(data_dict0['data'], s=5)

In [7]:
# data_name = 'hemisphere'
# np.savez(f"../../data/{data_name}.npz", **data_dict0)

In [23]:
def gradually_add(data, noise_rate=1, seed=42, noise='gaussian'):
    np.random.shuffle(data)
    np.random.seed(seed)
    noise_rates = np.random.rand(data.shape[0], 1) * noise_rate
    if noise == 'gaussian':
        data_std = data.std()
        noise = np.random.randn(*data.shape)
        data_noisy = data + noise * noise_rates * data_std
    elif noise == 'hi-freq':
        diff_map_op = DiffusionMap(n_components=3, t=3, random_state=seed).fit(data)
        data_noisy = data + make_hi_freq_noise(data, diff_map_op, noise_rate=noise_rates, add_data_mean=False)
    else:
        raise ValueError(f"Unknown noise type: {noise}")
    return data_noisy, noise_rates.flatten()

In [9]:
seed = 32
noise_level = 1.
data1 = data_dict0['data'].copy()
data1[:,2] = 0.
noisy, levels = gradually_add(data1, noise_rate=1.1, seed=seed, noise='gaussian')

In [10]:
scatter(noisy, levels, s=1, rescale=False)

In [24]:
noisy, levels = gradually_add(data_dict0['data'], noise_rate=1.1, seed=seed, noise='gaussian')
noisy2, levels2 = gradually_add(data_dict0['data'], noise_rate=1.1, seed=seed+1, noise='gaussian')
noisy = np.r_[noisy, noisy2]
levels = np.r_[levels, levels2]

In [25]:
scatter(noisy, levels, s=1)

In [26]:
dists = np.zeros((noisy.shape[0], noisy.shape[0]))
data_dict1 = dict(
    data=noisy,
    mask_x=levels,
    is_train = np.ones(noisy.shape[0], dtype=bool),
    dist = dists,
    colors=levels,
)

In [27]:
save_folder = f'../data/noise_predictor/'
pathlib.Path(save_folder).mkdir(parents=True, exist_ok=True)
data_name = 'hemisphere_gaussian'
np.savez(f"{save_folder}/{data_name}.npz", **data_dict1)

In [29]:
noisy, levels = gradually_add(data_dict0['data'], noise_rate=1.1, seed=seed, noise='gaussian')
noisy2, levels2 = gradually_add(data_dict0['data'], noise_rate=1.1, seed=seed+1, noise='gaussian')
noisy = np.r_[noisy, noisy2]
levels = np.r_[levels, levels2]
scatter(noisy, levels, s=1).show()
dists = np.zeros((noisy.shape[0], noisy.shape[0]))
data_dict2 = dict(
    data=noisy,
    mask_x=levels,
    is_train = np.ones(noisy.shape[0], dtype=bool),
    dist = dists,
    colors=levels,
)
data_name = 'hemisphere_hi_freq'
np.savez(f"{save_folder}/{data_name}.npz", **data_dict2)

In [32]:
data_name = 'hemisphere_ae'
np.savez(f"{save_folder}/{data_name}.npz", **data_dict0)